### 1. Import the libraries

In [71]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files



from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

# import k-means from clustering stage
from sklearn.cluster import KMeans

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    ------------------------------------------------------------
                       

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')


Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
neighborhoods_data = newyork_data['features']

In [5]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)      

In [6]:
neighborhoods.head()

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [7]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [8]:
# Print how many boroughs and neighborhoods the dataset has
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [37]:
# Now Print the geo location of Bronx located in Manhattan
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


##  Use Foursquare credentials to 

In [82]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 
CLIENT_SECRET:


In [38]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

In [14]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [39]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            100)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [40]:
#Get venues for all neighborhoods in our dataset
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                latitudes=manhattan_data['Latitude'],
                                longitudes=manhattan_data['Longitude'])

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [41]:
#Check size of resulting dataframe
manhattan_venues.shape

(3184, 7)

In [42]:
manhattan_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066      Starbucks   
4  Marble Hill              40.876551               -73.91066        Dunkin'   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877531       -73.905582    Coffee Shop  
4       40.877136       -73.906666     Donut Shop

In [43]:


#Number of venues per neighborhood
manhattan_venues.groupby('Neighborhood').count()



Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       75                      75     75   
Carnegie Hill                           89                      89     89   
Central Harlem                          43                      43     43   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             40                      40     40   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                93                      93     93   
Greenwich Village                      100                     100    100   
Hamilton Heights                        59                      59     59   
Hudson Yards                            55                      55     55   
Inwood                                  56                      56     56   
Lenox Hill                             100                     100    100   
Lincoln Square                          92                      92     92   
Little Italy                           100                     100    100   
Lower East Side                         48                      48     48   
Manhattan Valley                        46                      46     46   
Manhattanville                          45                      45     45   
Marble Hill                             25                      25     25   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     41                      41     41   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        28                      28     28   
Soho                                   100                     100    100   
Stuyvesant Town                         19                      19     19   
Sutton Place                           100                     100    100   
Tribeca                                 84                      84     84   
Tudor City                              80                      80     80   
Turtle Bay                             100                     100    100   
Upper East Side                         94                      94     94   
Upper West Side                         86                      86     86   
Washington Heights                      86                      86     86   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                75               75              75  
Carnegie Hill                    89               89              89  
Central Harlem                   43               43              43  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      40               40              40  
East Village                    100              100             100  
Finan

In [44]:
#Number of unique venue categories
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 325 uniques categories.


In [45]:
#print out the list of categories
manhattan_venues['Venue Category'].unique()[:100]

array(['Pizza Place', 'Yoga Studio', 'Diner', 'Coffee Shop', 'Donut Shop',
       'Gym', 'Tennis Stadium', 'Pharmacy', 'Department Store',
       'Discount Store', 'Supplement Shop', 'Seafood Restaurant',
       'Sandwich Place', 'Ice Cream Shop', 'Video Game Store',
       'Miscellaneous Shop', 'Steakhouse', 'Kids Store', 'Big Box Store',
       'Shopping Mall', 'Deli / Bodega', 'Hotel', 'Greek Restaurant',
       'Cocktail Bar', 'Chinese Restaurant', 'Spa', 'Bakery', 'Tea Room',
       'American Restaurant', 'New American Restaurant',
       'Hotpot Restaurant', 'Indie Movie Theater', 'Roof Deck',
       'Spanish Restaurant', 'Bubble Tea Shop', 'Noodle House', 'Museum',
       'Asian Restaurant', 'Bike Shop', 'Salon / Barbershop', 'Boutique',
       'Furniture / Home Store', 'Vietnamese Restaurant',
       'Thai Restaurant', 'Historic Site', 'Dessert Shop',
       'Italian Restaurant', 'Music Venue', 'Cosmetics Shop',
       'Supermarket', 'Korean Restaurant', 'Malay Restaurant',
   

In [50]:
# check if the results contain "Bar"

"Bar" in manhattan_venues['Venue Category'].unique()

True

In [51]:
# one hot encoding
to_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(3184, 326)


Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0   Marble Hill                  0               0                  0   
1   Marble Hill                  0               0                  0   
2   Marble Hill                  0               0                  0   
3   Marble Hill                  0               0                  0   
4   Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0                   0                    0             0                 0   
1                   0                    0             0                 0   
2                   0                    0             0                 0   
3                   0                    0             0                 0   
4                   0                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0           0       0     0    0   
1                    0          0           0           0       0     0    0   
2                    0          0           0           0       0     0    0   
3                    0          0           0           0       0     0    0   
4                    0          0           0           0       0     0    0   

   Baseball Field  Basketball Court  Beer Bar  Beer Garden  Beer Store  \
0               0                 0         0            0           0   
1               0                 0         0            0           0   
2               0                 0         0            0           0   
3               0                 0         0            0           0   
4               0                 0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0           0              0          0         0           0   
1           0              0          0         0           0   
2           0              0          0         0           0   
3           0              0          0         0           0   
4           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  \
0                     0               0            0       0                0   
1                     0               0            0       0                0   
2                     0               0            0       0                0   
3                     0               0            0       0          

In [55]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(40, 326)


Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000            0.00               0.00   
1         Carnegie Hill           0.000000            0.00               0.00   
2        Central Harlem           0.000000            0.00               0.00   
3               Chelsea           0.000000            0.00               0.00   
4             Chinatown           0.000000            0.00               0.00   
5          Civic Center           0.000000            0.00               0.00   
6               Clinton           0.000000            0.00               0.00   
7           East Harlem           0.000000            0.00               0.00   
8          East Village           0.000000            0.00               0.00   
9    Financial District           0.000000            0.00               0.00   
10             Flatiron           0.000000            0.00               0.00   
11             Gramercy           0.000000            0.00               0.00   
12    Greenwich Village           0.000000            0.00               0.00   
13     Hamilton Heights           0.000000            0.00               0.00   
14         Hudson Yards           0.000000            0.00               0.00   
15               Inwood           0.000000            0.00               0.00   
16           Lenox Hill           0.000000            0.00               0.01   
17       Lincoln Square           0.000000            0.00               0.00   
18         Little Italy           0.000000            0.00               0.00   
19      Lower East Side           0.000000            0.00               0.00   
20     Manhattan Valley           0.000000            0.00               0.00   
21       Manhattanville           0.000000            0.00               0.00   
22          Marble Hill           0.000000            0.00               0.00   
23              Midtown           0.000000            0.00               0.00   
24        Midtown South           0.000000            0.00               0.00   
25  Morningside Heights           0.000000            0.00               0.00   
26          Murray Hill           0.000000            0.00               0.00   
27                 Noho           0.000000            0.00               0.00   
28     Roosevelt Island           0.000000            0.00               0.00   
29                 Soho           0.000000            0.00               0.00   
30      Stuyvesant Town           0.000000            0.00               0.00   
31         Sutton Place           0.000000            0.01               0.00   
32              Tribeca           0.000000            0.00               0.00   
33           Tudor City           0.000000            0.00               0.00   
34           Turtle Bay           0.000000            0.00               0.00   
35      Upper East Side           0.000000            0.00               0.00   
36      Upper West Side           0.000000            0.00               0.00   
37   Washington Heights           0.011628            0.00               0.00   
38         West Village           0.010000            0.00               0.00   
39            Yorkville           0.000000            0.00               0.00   

    African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0             0.000000             0.013333          0.00          0.000000   
1             0.000000             0.011236          0.00          0.000000   
2             0.069767             0.046512          0.00          0.000000   
3             0.000000             0.040000          0.00          0.010000   
4             0.000000             0.030000          0.00          0.000000   
5             0.000000             0.020000          0.01          0.000000   
6             0.000000             0.040000          0.00          0.000000   
7             0.000000             0.000000          0.0

In [54]:
len(to_grouped[to_grouped["Bar"] > 0])

26

In [57]:
only_bars = to_grouped[["Neighborhoods","Bar"]]

In [58]:
only_bars.head()

Neighborhoods       Bar
0  Battery Park City  0.013333
1      Carnegie Hill  0.011236
2     Central Harlem  0.046512
3            Chelsea  0.020000
4          Chinatown  0.020000

In [59]:
# set number of clusters
toclusters = 4

to_clustering = only_bars.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 2, 1, 2, 2, 0, 2, 0, 3, 2], dtype=int32)

In [62]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = only_bars.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [63]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood       Bar  Cluster Labels
0  Battery Park City  0.013333               2
1      Carnegie Hill  0.011236               2
2     Central Harlem  0.046512               1
3            Chelsea  0.020000               2
4          Chinatown  0.020000               2

In [65]:
# merge to add latitude/longitude for each neighborhood
to_merged = to_merged.join(manhattan_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(3184, 9)


Neighborhood       Bar  Cluster Labels  Neighborhood Latitude  \
0  Battery Park City  0.013333               2              40.711932   
0  Battery Park City  0.013333               2              40.711932   
0  Battery Park City  0.013333               2              40.711932   
0  Battery Park City  0.013333               2              40.711932   
0  Battery Park City  0.013333               2              40.711932   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -74.016869         Battery Park City Esplanade       40.711622   
0              -74.016869  Waterfront Plaza, Brookfield Place       40.713241   
0              -74.016869                         Hudson Eats       40.712666   
0              -74.016869            Equinox Brookfield Place       40.712704   
0              -74.016869             Brookfield Place (BFPL)       40.713240   

   Venue Longitude Venue Category  
0       -74.017907           Park  
0       -74.016241          Plaza  
0       -74.015901     Food Court  
0       -74.014995            Gym  
0       -74.015193  Shopping Mall

In [66]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(3184, 9)


Neighborhood       Bar  Cluster Labels  Neighborhood Latitude  \
18         Little Italy  0.000000               0              40.719324   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
10             Flatiron  0.000000               0              40.739673   
22          Marble Hill  0.000000               0              40.876551   
22          Marble Hill  0.000000               0              40.876551   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0              40.754691   
23              Midtown  0.000000               0          

In [67]:


# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors



In [74]:
# Now Print the geo location of Bronx located in New York
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

In [76]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [77]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

In [78]:


#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]



Neighborhood  Bar  Cluster Labels  Neighborhood Latitude  \
18         Little Italy  0.0               0              40.719324   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
10             Flatiron  0.0               0              40.739673   
22          Marble Hill  0.0               0              40.876551   
22          Marble Hill  0.0               0              40.876551   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
23              Midtown  0.0               0              40.754691   
22          Marble Hill  0.0       

In [79]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood       Bar  Cluster Labels  Neighborhood Latitude  \
39         Yorkville  0.050000               1              40.775930   
21    Manhattanville  0.044444               1              40.816934   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775930   
39         Yorkville  0.050000               1              40.775

In [81]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood       Bar  Cluster Labels  Neighborhood Latitude  \
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
16          Lenox Hill  0.010000               2              40.768113   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
33          Tudor City  0.012500               2              40.746917   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000               2              40.752042   
34          Turtle Bay  0.020000   

In [80]:
#Cluster 3
to_merged.loc[to_merged['Cluster Labels'] == 3]

Neighborhood       Bar  Cluster Labels  Neighborhood Latitude  \
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
30  Stuyvesant Town  0.105263               3              40.731000   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3              40.727847   
30  Stuyvesant Town  0.105263               3              40.731000   
30  Stuyvesant Town  0.105263               3              40.731000   
8      East Village  0.080000               3              40.727847   
30  Stuyvesant Town  0.105263               3              40.731000   
8      East Village  0.080000               3              40.727847   
8      East Village  0.080000               3  